In [1]:
# import osmnx as ox
import pandas as pd
import geopandas as gpd
import networkx as nx
import numpy as np
import warnings
import sys
import os
warnings.filterwarnings("ignore")
sys.stderr = open(os.devnull, 'w')

# local crs
local_crs = 32636

In [2]:
import geopandas as gpd
from shapely.ops import unary_union

# Загрузка данных
region = gpd.read_file('data/Границы_только_МР_Границы_ЛО_Без_воды.geojson', engine="pyogrio")
region = region.to_crs(epsg=3857)

# Создание буфера в 100 метров
region['geometry'] = region.geometry.buffer(100)

# Объединение геометрий
merged_geometry = unary_union(region.geometry)

# Создание нового GeoDataFrame с объединенной геометрией
region = gpd.GeoDataFrame(geometry=[merged_geometry], crs=3857)
region = region.to_crs(epsg=4326)
region.explore()



In [3]:
from shapely.geometry import MultiPolygon
from shapely.wkt import loads  # Если геометрия в формате WKT
import geopandas as gpd


# Упрощение всех геометрий в GeoDataFrame
region['geometry'] = region['geometry'].apply(lambda geom: geom.simplify(tolerance=0.05, preserve_topology=True))
region['geometry'] = region['geometry'].apply(lambda geom: geom.buffer(0))
# Проверка результатов
region.explore()

In [4]:
region = gpd.read_file('/Users/mvin/Code/PopFrame/examples/data/leningrad_oblast_boundary.geojson', engine="pyogrio")
region

bbox_north  bbox_south  bbox_east  bbox_west   place_id  osm_type  osm_id  \
0   61.329254   58.417336  35.701312      26.44  155408467  relation  176095   

        lat        lon     class            type  place_rank  importance  \
0  60.18533  32.392533  boundary  administrative           8    0.682348   

  addresstype              name  \
0       state  Leningrad Oblast   

                                        display_name  \
0  Leningrad Oblast, Northwestern Federal Distric...   

                                            geometry  
0  MULTIPOLYGON (((26.44000 59.93833, 26.62887 59...

In [5]:
towns = gpd.read_file('data/towns.geojson', engine="pyogrio")
towns = towns.drop(columns=['population'])
towns = towns.rename(columns={'rounded_population': 'population'})
# adj_mx = pd.read_pickle('data/acc_mx.pickle')
# adj_mx.index = towns.index
# adj_mx.columns = towns.index

In [6]:
import requests
async def get_accessibility_matrix(region_id : int, graph_type : str) -> pd.DataFrame:
        res = requests.get('http://10.32.1.65:5700' + f'/api_v1/{region_id}/get_matrix', {
          'graph_type': graph_type
        })
        json = res.json()
        return pd.DataFrame(json['values'], index=json['index'], columns=json['columns'])

adj_mx = await get_accessibility_matrix(1, 'drive')

In [7]:
adj_mx

207      208      209      210      211      212      213      214   \
207     0.000   11.687   12.024   10.794    7.768    3.431   21.873   29.029   
208    11.687    0.000    0.337    4.313   18.027   13.690   29.914   37.070   
209    12.024    0.337    0.000    4.650   18.364   14.027   30.251   37.407   
210    10.794    4.313    4.650    0.000   17.134   12.797   29.021   36.177   
211     7.768   18.027   18.364   17.134    0.000    4.337   28.213   35.369   
...       ...      ...      ...      ...      ...      ...      ...      ...   
3133  195.417  184.351  184.014  188.043  201.757  197.420  213.644  220.800   
3134  189.116  178.050  177.713  181.742  195.456  191.119  207.343  214.499   
3135  172.899  161.833  161.496  165.525  179.239  174.902  191.126  198.282   
3136  171.556  160.490  160.153  164.182  177.896  173.559  189.783  196.939   
3137  183.444  172.378  172.041  176.070  189.784  185.447  201.671  208.827   

         215      216   ...     3128     3129     3130     3131     3132  \
207     8.415   17.122  ...  175.052  167.133  165.000  170.273  195.276   
208    16.456   10.347  ...  163.986  156.067  153.934  159.207  184.210   
209    16.248   10.684  ...  163.649  155.730  153.597  158.870  183.873   
210    15.563    9.748  ...  167.678  159.759  157.626  162.899  187.902   
211    14.755   23.462  ...  181.392  173.473  171.340  176.613  201.616   
...       ...      ...  ...      ...      ...      ...      ...      ...   
3133  197.759  194.077  ...   24.994   29.115   31.820   32.255    0.000   
3134  191.458  187.776  ...   17.942   22.063   24.768   25.203   17.446   
3135  175.241  171.559  ...   18.603   10.684    7.755   13.824   39.579   
3136  173.898  170.216  ...   17.260    9.341    6.412   12.481   38.236   
3137  185.786  182.104  ...   12.270   16.391   19.096   19.531   32.096   

         3133     3134     3135     3136     3137  
207   195.276  188.976  172.755  171.412  183.300  
208   184.210  177.910  161.689  160.346  172.234  
209   183.873  177.573  161.352  160.009  171.897  
210   187.902  181.602  165.381  164.038  175.926  
211   201.616  195.316  179.095  177.752  189.640  
...       ...      ...      ...      ...      ...  
3133    0.000   17.446   39.575   38.232   32.092  
3134   17.446    0.000   32.523   31.180   25.040  
3135   39.579   32.527    0.000    1.343   26.851  
3136   38.236   31.184    1.343    0.000   25.508  
3137   32.096   25.044   26.851   25.508    0.000  

[2930 rows x 2930 columns]

In [8]:
adj_mx.index = towns.index
adj_mx.columns = towns.index

In [28]:
adj_mx.loc[36,2].round(3)

inf

In [27]:
towns[towns['name'] == 'Головачово']

geometry        name  population  \
36  POINT (637710.906 6600196.994)  Головачово          39   

                       level  
36  Малое сельское поселение

In [9]:
from popframe.preprocessing.level_filler import LevelFiller
level_filler = LevelFiller(towns=towns)
towns = level_filler.fill_levels()
towns

geometry             name  population  \
0     POINT (33.75892 59.36226)           Болото          10   
1     POINT (33.78600 59.47517)   Большой Остров          68   
2     POINT (33.79236 59.47356)              Бор        1734   
3     POINT (33.77572 59.44249)        Бороватое          10   
4     POINT (33.67728 59.32819)           Бочево          10   
...                         ...              ...         ...   
2925  POINT (31.23421 59.17021)     Апраксин Бор         313   
2926  POINT (31.31924 59.18702)    Александровка         313   
2927  POINT (31.47462 59.29408)    Большая Горка         313   
2928  POINT (31.46265 59.30308)         Дроздово           5   
2929  POINT (31.45747 59.30139)  Большая Кунесть           5   

                           level  
0       Малое сельское поселение  
1       Малое сельское поселение  
2     Большое сельское поселение  
3       Малое сельское поселение  
4       Малое сельское поселение  
...                          ...  
2925  Среднее сельское поселение  
2926  Среднее сельское поселение  
2927  Среднее сельское поселение  
2928    Малое сельское поселение  
2929    Малое сельское поселение  

[2930 rows x 4 columns]

In [10]:
crs = towns.estimate_utm_crs()
region = region.to_crs(crs)
towns = towns.to_crs(crs)

In [11]:
from popframe.method.popuation_frame import PopulationFrame
from popframe.models.region import Region

region_model = Region(
  region = region,
  towns=towns,
  accessibility_matrix=adj_mx
)
# region.to_pickle('Ленинградская область.pickle')
# region_model = Region.from_pickle('data/Ленинградская область.pickle')

In [12]:
region_model.get_towns_gdf()

id             name  population                       level  \
0        0           Болото          10    Малое сельское поселение   
1        1   Большой Остров          68    Малое сельское поселение   
2        2              Бор        1734  Большое сельское поселение   
3        3        Бороватое          10    Малое сельское поселение   
4        4           Бочево          10    Малое сельское поселение   
...    ...              ...         ...                         ...   
2925  2925     Апраксин Бор         313  Среднее сельское поселение   
2926  2926    Александровка         313  Среднее сельское поселение   
2927  2927    Большая Горка         313  Среднее сельское поселение   
2928  2928         Дроздово           5    Малое сельское поселение   
2929  2929  Большая Кунесть           5    Малое сельское поселение   

                            geometry  
0     POINT (543142.343 6580637.216)  
1     POINT (544532.933 6593227.683)  
2     POINT (544895.406 6593052.346)  
3     POINT (543993.115 6589581.591)  
4     POINT (538540.114 6576793.156)  
...                              ...  
2925  POINT (399059.733 6560340.947)  
2926  POINT (403967.163 6562086.557)  
2927  POINT (413116.733 6573792.753)  
2928  POINT (412458.024 6574810.780)  
2929  POINT (412158.902 6574629.673)  

[2930 rows x 5 columns]

In [13]:
frame_method = PopulationFrame(region=region_model)
G = frame_method.build_network_frame()
num_edges = G.number_of_edges()
print("Количество рёбер в графе:", num_edges)
output = frame_method.build_circle_frame(output_type='gdf') 
output

Количество рёбер в графе: 2929


id             name  population                       level  \
0        0           Болото          10    Малое сельское поселение   
1        1   Большой Остров          68    Малое сельское поселение   
2        2              Бор        1734  Большое сельское поселение   
3        3        Бороватое          10    Малое сельское поселение   
4        4           Бочево          10    Малое сельское поселение   
...    ...              ...         ...                         ...   
2925  2925     Апраксин Бор         313  Среднее сельское поселение   
2926  2926    Александровка         313  Среднее сельское поселение   
2927  2927    Большая Горка         313  Среднее сельское поселение   
2928  2928         Дроздово           5    Малое сельское поселение   
2929  2929  Большая Кунесть           5    Малое сельское поселение   

                                               geometry  
0     POLYGON ((3758096.407 8259101.277, 3758096.068...  
1     POLYGON ((3761223.571 8283806.182, 3761222.687...  
2     POLYGON ((3762675.072 8283452.668, 3762670.608...  
3     POLYGON ((3759966.352 8276646.700, 3759966.013...  
4     POLYGON ((3749008.396 8251662.279, 3749008.057...  
...                                                 ...  
2925  POLYGON ((3477369.731 8217266.893, 3477367.834...  
2926  POLYGON ((3486835.777 8220918.561, 3486833.881...  
2927  POLYGON ((3504132.564 8244221.253, 3504130.667...  
2928  POLYGON ((3502455.718 8246184.181, 3502455.479...  
2929  POLYGON ((3501879.399 8245816.132, 3501879.159...  

[2930 rows x 5 columns]

In [14]:
from popframe.method.aglomeration import AgglomerationAnalysis

agglomeration = AgglomerationAnalysis(region=region_model)
agglomerations_gdf = agglomeration.build_agglomeration_voronoi(G)


In [15]:
frame_method.get_graph_html(G, 'final_graph_with_legend.html')

In [16]:
m = agglomerations_gdf.explore()
towns.explore(m=m)

In [17]:
from popframe.method.territory_evaluation import TerritoryEvaluation
from popframe.models.region import Region
from shapely.geometry import shape


geojson_data = {
    "geometry": {
        "type": "Polygon",
        "coordinates": [
            [
                [29.982879431084967, 59.363554752593245],
                [29.982879431084967, 59.322083801173534],
                [30.109075699649765, 59.322083801173534],
                [30.109075699649765, 59.363554752593245],
                [29.982879431084967, 59.363554752593245]
            ]
        ]
    },
    "properties": {},
    "type": "Feature"
}

# Преобразуем словарь в геометрию
geom = shape(geojson_data['geometry'])

# Создаем GeoDataFrame
territories_gdf = gpd.GeoDataFrame([{'geometry': geom}], crs='EPSG:4326')

evaluation = TerritoryEvaluation(region=region_model)
# Пример вызова функции
results = evaluation.population_criterion(territories_gdf=territories_gdf)
results

[{'project': None,
  'average_population_density': 17.2,
  'total_population': 39739,
  'score': 4.0,
  'interpretation': 'Территория имеет хорошие показатели численности и плотности населения, что способствует ее активному развитию.'}]

In [18]:
from popframe.method.territory_evaluation import TerritoryEvaluation
from popframe.models.region import Region
from shapely.geometry import shape


geojson_data = {
    "geometry": {
        "type": "Polygon",
        "coordinates": [
            [
                [29.982879431084967, 59.363554752593245],
                [29.982879431084967, 59.322083801173534],
                [30.109075699649765, 59.322083801173534],
                [30.109075699649765, 59.363554752593245],
                [29.982879431084967, 59.363554752593245]
            ]
        ]
    },
    "properties": {},
    "type": "Feature"
}

geom = shape(geojson_data['geometry'])

# Создаем GeoDataFrame
territories_gdf = gpd.GeoDataFrame([{'geometry': geom}], crs='EPSG:4326')

result = evaluation.evaluate_territory_location(territories_gdf=territories_gdf)
result

[{'territory': 'None',
  'score': 5,
  'interpretation': 'Территория находится внутри или непосредственной близости населенного пункта уровня Малый город',
  'closest_settlement': 'Сиверский',
  'closest_settlement1': None,
  'closest_settlement2': None}]